Author: Aditya Joshi

In [1]:
import numpy as np
import tensorflow as tf

In [18]:
def cnn_model_fn(features, labels, mode):
    input_layer = tf.reshape(features["x"],[-1,28,28,1])
    conv1 = tf.layers.conv2d(inputs = input_layer, filters=32, kernel_size=[5,5], padding='same', activation=tf.nn.relu)
    
    pool1 = tf.layers.max_pooling2d(inputs=conv1,pool_size=[2,2],strides=2)
    
    conv2 = tf.layers.conv2d(inputs = pool1,filters=64,kernel_size=[5,5],padding='same',activation=tf.nn.relu)
    
    pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2,2], strides=2)
    
    pool2_flat = tf.reshape(pool2,[-1, 7 * 7 * 64])
    dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)
    dropout = tf.layers.dropout(inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)
    logits = tf.layers.dense(inputs=dropout, units = 10)
    predictions = {'classes': tf.argmax(input=logits, axis=1),
                    'probabilities': tf.nn.softmax(logits, name='softmax_tensor')}
    
    if mode == tf.estimator.ModeKeys.PREDICT:
        return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)
    loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)
    
    if mode == tf.estimator.ModeKeys.TRAIN:
        optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
        train_op = optimizer.minimize(loss=loss, global_step = tf.train.get_global_step())
        return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)
    
    eval_metric_ops = {'accuracy': tf.metrics.accuracy(labels=labels,predictions=predictions['classes'])}
    return tf.estimator.EstimatorSpec(mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)

In [12]:
mnist = tf.contrib.learn.datasets.load_dataset("mnist")
train_data = mnist.train.images

Extracting MNIST-data/train-images-idx3-ubyte.gz
Extracting MNIST-data/train-labels-idx1-ubyte.gz
Extracting MNIST-data/t10k-images-idx3-ubyte.gz
Extracting MNIST-data/t10k-labels-idx1-ubyte.gz


In [13]:
tf.logging.set_verbosity(tf.logging.INFO)

In [19]:
train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
eval_data = mnist.test.images
eval_labels = np.asarray(mnist.test.labels,dtype=np.int32)
mnist_classifier = tf.estimator.Estimator(model_fn=cnn_model_fn, model_dir="/tmp/mnist_convnet_model")
tensors_to_log = {"probabilities": "softmax_tensor"}
logging_hook = tf.train.LoggingTensorHook(tensors=tensors_to_log, every_n_iter=50)
train_input_fn = tf.estimator.inputs.numpy_input_fn(x={"x": train_data},
    y=train_labels,
    batch_size=100,
    num_epochs=None,
    shuffle=True)
mnist_classifier.train(
    input_fn=train_input_fn,
    steps=20000,
    hooks=[logging_hook])

INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_save_checkpoints_secs': 600, '_session_config': None, '_keep_checkpoint_max': 5, '_task_type': 'worker', '_is_chief': True, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x1c1ebe9290>, '_save_checkpoints_steps': None, '_keep_checkpoint_every_n_hours': 10000, '_service': None, '_num_ps_replicas': 0, '_tf_random_seed': None, '_master': '', '_num_worker_replicas': 1, '_task_id': 0, '_log_step_count_steps': 100, '_model_dir': '/tmp/mnist_convnet_model', '_save_summary_steps': 100}
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Saving checkpoints for 1 into /tmp/mnist_convnet_model/model.ckpt.
INFO:tensorflow:probabilities = [[ 0.08521545  0.10904448  0.10077114  0.11851019  0.08464319  0.10352702
   0.09692895  0.09972919  0.11179434  0.08983606]
 [ 0.09572121  0.0881011   0.1015598   0.1077739   0.10035416  0.11509147
   0.09305747  0.09276856  0.12029149  0.0852809 ]
 [ 0.1

INFO:tensorflow:loss = 2.31397, step = 1
INFO:tensorflow:probabilities = [[ 0.09488532  0.09424815  0.09540009  0.11182267  0.09190805  0.09763239
   0.10401675  0.09425218  0.11388715  0.10194723]
 [ 0.10168932  0.09795313  0.10023073  0.10255334  0.09244358  0.09962483
   0.1142566   0.08178615  0.11778376  0.09167855]
 [ 0.1053652   0.0924318   0.09557763  0.10361614  0.08924528  0.09990965
   0.09347177  0.09325568  0.12993886  0.09718802]
 [ 0.09073643  0.10841423  0.09206957  0.09779596  0.09468803  0.10033882
   0.09075108  0.08732153  0.13980034  0.0980839 ]
 [ 0.11130694  0.09740417  0.08863968  0.10745626  0.09082631  0.10364518
   0.09521669  0.09579928  0.10710274  0.10260275]
 [ 0.10381759  0.09472095  0.08912311  0.1047366   0.09196242  0.09999376
   0.10442312  0.09077571  0.12093706  0.09950963]
 [ 0.11349019  0.10129367  0.09481228  0.09581787  0.08606965  0.10075993
   0.09324199  0.09479641  0.12348417  0.09623388]
 [ 0.10183848  0.08693906  0.10486709  0.1144445   0

INFO:tensorflow:global_step/sec: 2.44577
INFO:tensorflow:probabilities = [[ 0.10382973  0.09480247  0.09758311  0.11253399  0.08608032  0.0979425
   0.09735627  0.08795039  0.12602584  0.09589538]
 [ 0.09691649  0.09375857  0.09774333  0.09466872  0.08866557  0.10393462
   0.10442349  0.08785221  0.14659317  0.08544374]
 [ 0.10085338  0.10215802  0.0902882   0.10935009  0.08383201  0.10296258
   0.09014507  0.10024493  0.11766962  0.1024961 ]
 [ 0.09273859  0.10452166  0.10766948  0.09949366  0.09802437  0.10750107
   0.09243232  0.09134653  0.11468069  0.09159164]
 [ 0.09072682  0.09702313  0.09479172  0.09490632  0.09717578  0.09219862
   0.10075273  0.0978027   0.12297264  0.11164957]
 [ 0.10434408  0.09033889  0.09537445  0.09384535  0.10117301  0.11045761
   0.08547352  0.09232659  0.12859893  0.09806762]
 [ 0.10819814  0.09428287  0.10910884  0.10788565  0.09449584  0.09867072
   0.09505305  0.08489205  0.11978667  0.08762618]
 [ 0.10480876  0.09080841  0.09574994  0.11525338  0.

INFO:tensorflow:loss = 2.29567, step = 101 (40.898 sec)
INFO:tensorflow:probabilities = [[ 0.09735161  0.09222009  0.09758819  0.1044237   0.08414928  0.11223464
   0.09378607  0.09230949  0.12900473  0.09693216]
 [ 0.11104294  0.08879338  0.09910526  0.10356741  0.09399577  0.10132703
   0.10515404  0.08923666  0.11022491  0.09755255]
 [ 0.0971805   0.09158087  0.10799714  0.10137644  0.09601115  0.10180393
   0.0926315   0.09955591  0.10899808  0.1028645 ]
 [ 0.09853388  0.10330224  0.09780874  0.11005054  0.09874644  0.10489774
   0.10142404  0.09629111  0.10214667  0.08679858]
 [ 0.11169218  0.0944476   0.1037569   0.1056791   0.07954857  0.10139214
   0.09655994  0.09332671  0.11739878  0.09619808]
 [ 0.10344531  0.09806589  0.08863851  0.10053051  0.09216974  0.10012598
   0.09682266  0.09824152  0.1215256   0.10043428]
 [ 0.11512642  0.09758852  0.09390575  0.10008056  0.097303    0.10640807
   0.09290867  0.09132855  0.11906851  0.08628195]
 [ 0.09287745  0.10236983  0.10569839

INFO:tensorflow:global_step/sec: 2.53689
INFO:tensorflow:probabilities = [[ 0.10360625  0.10620219  0.10412873  0.10919567  0.07991619  0.10150177
   0.10062534  0.09325124  0.10738532  0.0941873 ]
 [ 0.10775182  0.09153411  0.10275727  0.10958625  0.09528215  0.09678396
   0.10104537  0.09177494  0.1010727   0.10241141]
 [ 0.11997011  0.09239899  0.0878123   0.10705561  0.0954977   0.10844851
   0.09095915  0.10109077  0.11271763  0.08404919]
 [ 0.10005513  0.10424214  0.11076109  0.09766062  0.09358598  0.09972807
   0.09375926  0.09705961  0.1047381   0.09841003]
 [ 0.0964768   0.0989199   0.10149312  0.10593709  0.08940566  0.10624836
   0.10477769  0.0943519   0.1123905   0.08999904]
 [ 0.10763879  0.08482473  0.09755482  0.10879036  0.09147694  0.1024215
   0.09454015  0.10012767  0.11064565  0.10197945]
 [ 0.09761957  0.10389831  0.10153623  0.09762425  0.08660675  0.08713338
   0.10399302  0.10022042  0.11961139  0.10175669]
 [ 0.08418002  0.10138208  0.10011552  0.09424058  0.

...

INFO:tensorflow:global_step/sec: 2.66839
INFO:tensorflow:probabilities = [[ 0.00131923  0.00005319  0.0132837   0.00060822  0.00675608  0.00014308
   0.00053443  0.00205097  0.00826901  0.96698207]
 [ 0.01756034  0.00054593  0.00075598  0.00015431  0.00003129  0.97126728
   0.00206517  0.0037899   0.00377934  0.00005049]
 [ 0.00000433  0.00002123  0.01092986  0.00070806  0.00001674  0.00000108
   0.00003994  0.00001993  0.98822844  0.00003043]
 [ 0.00000002  0.00000284  0.00004781  0.00017586  0.00010926  0.00000082
   0.          0.9965629   0.00001696  0.00308356]
 [ 0.00000144  0.00293253  0.00198215  0.00399101  0.00001511  0.00002657
   0.00000006  0.99049628  0.00020533  0.0003495 ]
 [ 0.00003347  0.00030619  0.00021924  0.00003165  0.00233254  0.00002236
   0.00000132  0.8583526   0.0030651   0.13563552]
 [ 0.00011123  0.00020691  0.01133655  0.00003163  0.00067437  0.00446672
   0.22486898  0.0000049   0.75824845  0.00005028]
 [ 0.00000025  0.00000087  0.00000277  0.99066508  0

INFO:tensorflow:loss = 0.0662337, step = 19801 (37.477 sec)
INFO:tensorflow:probabilities = [[ 0.00290293  0.00000512  0.00003327  0.00244625  0.00050418  0.00075099
   0.0000024   0.21737467  0.00005974  0.77592045]
 [ 0.00000021  0.00000076  0.00030435  0.01070538  0.00015626  0.00010313
   0.00000507  0.0000096   0.98837739  0.00033783]
 [ 0.0000001   0.00000003  0.00000006  0.00000433  0.9983108   0.00002374
   0.00000024  0.00003207  0.00041584  0.00121279]
 [ 0.00000024  0.00000515  0.00006077  0.0000072   0.00000136  0.0000006
   0.          0.99866176  0.00000248  0.00126052]
 [ 0.00005585  0.00001682  0.99161547  0.00393598  0.0000002   0.00007319
   0.00008611  0.00000122  0.00421505  0.00000023]
 [ 0.0000064   0.00001194  0.00014803  0.00035044  0.00000453  0.00006647
   0.00003603  0.0000003   0.99934489  0.00003092]
 [ 0.00096517  0.00000645  0.99214023  0.00233451  0.0000287   0.00024662
   0.00422283  0.00000166  0.00005208  0.00000182]
 [ 0.00009079  0.0000294   0.00033

INFO:tensorflow:global_step/sec: 2.65648
INFO:tensorflow:probabilities = [[ 0.          0.00000063  0.00003097  0.00002339  0.          0.00000001
   0.          0.99991429  0.00000309  0.00002767]
 [ 0.00001     0.00001966  0.00009484  0.00033569  0.00000026  0.00001541
   0.          0.99916124  0.00001366  0.00034943]
 [ 0.00011849  0.99802041  0.00048528  0.00019398  0.00003451  0.00000654
   0.00001284  0.00008827  0.00103294  0.00000671]
 [ 0.00000002  0.00000002  0.00000114  0.00001063  0.00000002  0.00000005
   0.          0.99988425  0.00000324  0.00010057]
 [ 0.00001744  0.00000296  0.00013934  0.00000104  0.00007937  0.00015815
   0.9995963   0.00000014  0.00000399  0.00000139]
 [ 0.00061229  0.00015951  0.00281897  0.92159444  0.00000129  0.07128344
   0.00000244  0.00016339  0.00215617  0.00120807]
 [ 0.00001615  0.00001326  0.0000341   0.00451924  0.00371549  0.00017582
   0.00000076  0.19590129  0.00027451  0.79534948]
 [ 0.00000321  0.00558214  0.00008904  0.83098829  0

INFO:tensorflow:loss = 0.11146, step = 19901 (37.643 sec)
INFO:tensorflow:probabilities = [[ 0.00040211  0.00000305  0.01131881  0.8231284   0.          0.15963876
   0.00000001  0.0000131   0.00548973  0.00000597]
 [ 0.00001171  0.00000015  0.00002504  0.00000054  0.99968839  0.00000879
   0.00019345  0.00000312  0.00000196  0.00006688]
 [ 0.00000041  0.00019672  0.99956912  0.00003     0.00000434  0.00000048
   0.00000668  0.000192    0.00000026  0.        ]
 [ 0.00016699  0.01488742  0.00019898  0.00223534  0.00053139  0.05861119
   0.92156124  0.00001441  0.00176129  0.00003186]
 [ 0.02904849  0.00264283  0.00732855  0.69389522  0.00002713  0.25259018
   0.00106256  0.00096542  0.00157605  0.01086358]
 [ 0.0000335   0.00000046  0.00015328  0.0000029   0.0000954   0.00000818
   0.99969637  0.          0.0000099   0.00000001]
 [ 0.0000601   0.00000594  0.95587587  0.04351129  0.00004433  0.00008432
   0.0000461   0.00004438  0.00025578  0.00007189]
 [ 0.00000051  0.00000001  0.000025

INFO:tensorflow:Saving checkpoints for 20000 into /tmp/mnist_convnet_model/model.ckpt.
INFO:tensorflow:Loss for final step: 0.224131.


In [22]:
eval_input_fn = tf.estimator.inputs.numpy_input_fn(x = {"x":eval_data}, y = eval_labels, num_epochs = 1, shuffle = False)
eval_results = mnist_classifier.evaluate(input_fn = eval_input_fn)
print eval_results

INFO:tensorflow:Starting evaluation at 2018-04-04-06:45:44
INFO:tensorflow:Restoring parameters from /tmp/mnist_convnet_model/model.ckpt-20000
INFO:tensorflow:Finished evaluation at 2018-04-04-06:45:56
INFO:tensorflow:Saving dict for global step 20000: accuracy = 0.9711, global_step = 20000, loss = 0.0968972
{'loss': 0.096897222, 'global_step': 20000, 'accuracy': 0.97109997}


Reference: https://www.tensorflow.org/tutorials/layers